In [1]:
import os
import json

from tqdm import tqdm
import numpy as np
import sklearn
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder

from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.callbacks import TensorBoard

import cv2 as cv
import mediapipe as mp

## Preparing Data

In [2]:
# load data

json_path = './WLASL_v0.3.json'
videos_path = './videos'

with open(json_path, 'r') as file:
    json_data = json.load(file)

json_data

[{'gloss': 'book',
  'instances': [{'bbox': [385, 37, 885, 720],
    'fps': 25,
    'frame_end': -1,
    'frame_start': 1,
    'instance_id': 0,
    'signer_id': 118,
    'source': 'aslbrick',
    'split': 'train',
    'url': 'http://aslbricks.org/New/ASL-Videos/book.mp4',
    'variation_id': 0,
    'video_id': '69241'},
   {'bbox': [190, 25, 489, 370],
    'fps': 25,
    'frame_end': -1,
    'frame_start': 1,
    'instance_id': 1,
    'signer_id': 90,
    'source': 'aslsignbank',
    'split': 'train',
    'url': 'https://aslsignbank.haskins.yale.edu/dictionary/protected_media/glossvideo/ASL/BO/BOOK-418.mp4',
    'variation_id': 0,
    'video_id': '65225'},
   {'bbox': [262, 1, 652, 480],
    'fps': 25,
    'frame_end': -1,
    'frame_start': 1,
    'instance_id': 2,
    'signer_id': 110,
    'source': 'valencia-asl',
    'split': 'train',
    'url': 'https://www.youtube.com/watch?v=0UsjUE-TXns',
    'variation_id': 0,
    'video_id': '68011'},
   {'bbox': [123, 19, 516, 358],
    'fps

In [3]:
json_data[0]['gloss']

'book'

In [4]:
json_data[0]['instances']

[{'bbox': [385, 37, 885, 720],
  'fps': 25,
  'frame_end': -1,
  'frame_start': 1,
  'instance_id': 0,
  'signer_id': 118,
  'source': 'aslbrick',
  'split': 'train',
  'url': 'http://aslbricks.org/New/ASL-Videos/book.mp4',
  'variation_id': 0,
  'video_id': '69241'},
 {'bbox': [190, 25, 489, 370],
  'fps': 25,
  'frame_end': -1,
  'frame_start': 1,
  'instance_id': 1,
  'signer_id': 90,
  'source': 'aslsignbank',
  'split': 'train',
  'url': 'https://aslsignbank.haskins.yale.edu/dictionary/protected_media/glossvideo/ASL/BO/BOOK-418.mp4',
  'variation_id': 0,
  'video_id': '65225'},
 {'bbox': [262, 1, 652, 480],
  'fps': 25,
  'frame_end': -1,
  'frame_start': 1,
  'instance_id': 2,
  'signer_id': 110,
  'source': 'valencia-asl',
  'split': 'train',
  'url': 'https://www.youtube.com/watch?v=0UsjUE-TXns',
  'variation_id': 0,
  'video_id': '68011'},
 {'bbox': [123, 19, 516, 358],
  'fps': 25,
  'frame_end': 60,
  'frame_start': 1,
  'instance_id': 3,
  'signer_id': 113,
  'source': 'lil

In [5]:
# data exploration

import pandas as pd

df = pd.read_json(json_path)
df.head()

gloss                                          instances
0      book  [{'bbox': [385, 37, 885, 720], 'fps': 25, 'fra...
1     drink  [{'bbox': [551, 68, 1350, 1080], 'fps': 25, 'f...
2  computer  [{'bbox': [0, 0, 360, 240], 'fps': 25, 'frame_...
3    before  [{'bbox': [0, 0, 360, 240], 'fps': 25, 'frame_...
4     chair  [{'bbox': [0, 0, 360, 240], 'fps': 25, 'frame_...

In [6]:
# process data

processed_data = []

# show progress bar while iterating
for i in tqdm(range(len(json_data))):
    gloss = json_data[i]['gloss']
    instances = json_data[i]['instances']

    for instance in instances:
        # print(instance['video_id'])
        video_id = instance['video_id']
        
        if os.path.exists(os.path.join(videos_path, f'{video_id}.mp4')):
            video_path = os.path.join(videos_path, f'{video_id}.mp4')
            frame_start = instance['frame_start']
            frame_end = instance['frame_end']
            # split = instance['split']
            
            processed_data.append({
                'gloss': gloss,
                'video_id': video_id,
                'video_path': video_path,
                'frame_start': frame_start,
                'frame_end': frame_end,
                # 'split': split
            })

processed_data

100%|████████████████████████████████████| 2000/2000 [00:00<00:00, 40431.70it/s]


[{'gloss': 'book',
  'video_id': '69241',
  'video_path': './videos/69241.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'book',
  'video_id': '07069',
  'video_path': './videos/07069.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'book',
  'video_id': '07068',
  'video_path': './videos/07068.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'book',
  'video_id': '07070',
  'video_path': './videos/07070.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'book',
  'video_id': '07099',
  'video_path': './videos/07099.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'book',
  'video_id': '07074',
  'video_path': './videos/07074.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'drink',
  'video_id': '69302',
  'video_path': './videos/69302.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'drink',
  'video_id': '65539',
  'video_path': './videos/65539.mp4',
  'frame_start': 1,
  'frame_end': -1},
 {'gloss': 'drink',
  'video_id': '177

In [7]:
len(processed_data)

11980

In [8]:
# write data to csv file

with open('./processed_data.json', 'w') as file:
    json.dump(processed_data, file, indent=4)

## Landmark Extraction Using MediaPipe

In [9]:
mp_holistic = mp.solutions.holistic

In [10]:
NUM_FACE_LANDMARKS = 468
NUM_HAND_LANDMARKS = 21
NUM_POSE_LANDMARKS = 33
TOTAL_LANDMARKS = NUM_FACE_LANDMARKS + NUM_HAND_LANDMARKS * 2 + NUM_POSE_LANDMARKS

def extract_frame_keypoints(all_landmarks):
    left_hand_arr = np.zeros(NUM_HAND_LANDMARKS * 3)
    right_hand_arr = np.zeros(NUM_HAND_LANDMARKS * 3)
    face_arr = np.zeros(NUM_FACE_LANDMARKS * 3)
    pose_arr = np.zeros(NUM_POSE_LANDMARKS * 4)
    
    #left hand
    if all_landmarks.left_hand_landmarks:
        left_hand_arr = np.array([[pos.x, pos.y, pos.z] for pos in all_landmarks.left_hand_landmarks.landmark]).flatten()
        # print('left', left_hand_arr.shape)

    # right hand
    if all_landmarks.right_hand_landmarks:
        right_hand_arr = np.array([[pos.x, pos.y, pos.z] for pos in all_landmarks.right_hand_landmarks.landmark]).flatten()
        # print('right', right_hand_arr.shape)

    # face
    if all_landmarks.face_landmarks:
        face_arr = np.array([[pos.x, pos.y, pos.z] for pos in all_landmarks.face_landmarks.landmark]).flatten()
        # print(face_arr.shape)
    
    # pose
    if all_landmarks.pose_landmarks:
        pose_arr = np.array([[pos.x, pos.y, pos.z, pos.visibility] for pos in all_landmarks.pose_landmarks.landmark]).flatten()
        # print(pose_arr.shape)

    return np.concatenate([left_hand_arr, right_hand_arr, face_arr, pose_arr])

def extract_video_keypoints(video_path, start=1, end=-1):
    cap = cv.VideoCapture(video_path)
    
    if start < 1 or start > int(cap.get(cv.CAP_PROP_FRAME_COUNT)):
        start = 1
 
    if end < min(0, start):
        end = int(cap.get(cv.CAP_PROP_FRAME_COUNT))
    
    num_frames = end - start + 1
    keypoints_arr_size = NUM_HAND_LANDMARKS * 3 + NUM_HAND_LANDMARKS * 3 + NUM_FACE_LANDMARKS * 3 + NUM_POSE_LANDMARKS * 4
    video_keypoints = np.zeros((num_frames, keypoints_arr_size))

    frame_index = 1
    
    # Set mediapipe model
    with mp_holistic.Holistic(
        min_detection_confidence=0.5,
        min_tracking_confidence=0.5) as holistic_model:
        while cap.isOpened() and frame_index <= end:
    
            # Read feed
            success, frame = cap.read()

            if not success:
                print("Failed to read frame.")
                break

            if frame_index >= start:
                frame.flags.writeable = False
                frame = cv.cvtColor(frame, cv.COLOR_BGR2RGB)
                frame_landmarks = holistic_model.process(frame)
                keypoints_arr = extract_frame_keypoints(frame_landmarks)
                video_keypoints[frame_index - start] = keypoints_arr

            frame_index += 1
                
        cap.release()
        cv.destroyAllWindows()
    return video_keypoints
    

In [11]:
# test

results = extract_video_keypoints('./videos/13799.mp4')
results.shape

I0000 00:00:1704813945.868750       1 gl_context.cc:344] GL version: 2.1 (2.1 Metal - 88), renderer: Apple M3
INFO: Created TensorFlow Lite XNNPACK delegate for CPU.


(34, 1662)

## Save Video Keypoints as Numpy Arrays

In [12]:
dest_dir = './keypoints'
os.makedirs(dest_dir, exist_ok=True)

In [ ]:
for i in tqdm(range(len(processed_data)), ncols=100):
# for i in range(100):
    video_id = processed_data[i]['video_id']
    npy_path = os.path.join(dest_dir, f'{video_id}.npy')
    
    if not os.path.exists(npy_path): 
        video_path = processed_data[i]['video_path']
        start = processed_data[i]['frame_start']
        end = processed_data[i]['frame_end']
    
        try:
            video_keypoints = extract_video_keypoints(video_path, start, end)
            print(npy_path)
            np.save(npy_path, video_keypoints)
            
        except Exception as e:
            print(f"Failed on video at {video_path}:{e}")
            continue

  1%|▍                                                         | 101/11980 [00:00<01:56, 101.92it/s]

./keypoints/08924.npy


I0000 00:00:1704814590.705799       1 gl_context.cc:344] GL version: 2.1 (2.1 Metal - 88), renderer: Apple M3


./keypoints/65299.npy


I0000 00:00:1704814592.374361       1 gl_context.cc:344] GL version: 2.1 (2.1 Metal - 88), renderer: Apple M3


...

I0000 00:00:1704818980.492502       1 gl_context.cc:344] GL version: 2.1 (2.1 Metal - 88), renderer: Apple M3
 18%|█████████▉                                            | 2191/11980 [1:13:12<4:07:09,  1.51s/it]

./keypoints/48904.npy


I0000 00:00:1704818982.257691       1 gl_context.cc:344] GL version: 2.1 (2.1 Metal - 88), renderer: Apple M3
 18%|█████████▉                                            | 2192/11980 [1:13:13<4:03:10,  1.49s/it]

Failed to read frame.
./keypoints/48907.npy


I0000 00:00:1704818983.690516       1 gl_context.cc:344] GL version: 2.1 (2.1 Metal - 88), renderer: Apple M3


## Preprocess Data

In [14]:
import pandas as pd

df = pd.read_json(json_path)
glosses = df['gloss'].unique()

In [15]:
len(glosses)

2000

In [16]:
target_frames = 50
step = 10
padding_value = 0

data_sequence = []
label_sequence = []

landmarks_dir = './keypoints/'

print(len(processed_data))

for entry in processed_data:
    video_id = entry['video_id']
    npy_path = landmarks_dir + video_id + '.npy'

    # if the numpy array of landmakrs exist, record the label and load the array
    if os.path.exists(npy_path):
        print(npy_path)
        npy_arr = np.load(npy_path)
        num_frames = npy_arr.shape[0]

        # not enough frames
        if num_frames < target_frames:
            npy_arr = np.pad(npy_arr, ((0, target_frames - num_frames), (0, 0)), mode='constant', constant_values=padding_value)
            print(npy_arr.shape)
            # num_frames = target_frames

        # extra frames
        if num_frames > target_frames:
            for start_index in range(0, num_frames - target_frames + 1, step):
                end = start_index + target_frames
                # print(npy_arr[start_index:end].shape)
                data_sequence.append(npy_arr[start_index:end])
                label_sequence.append(entry['gloss'])
        
        if num_frames == target_frames:
            print(50)
            
print(len(data_sequence) == len(label_sequence))
print(np.array(data_sequence).shape)
print(np.array(label_sequence).shape)

11980
./keypoints/69241.npy
./keypoints/07069.npy
(50, 1662)
./keypoints/07068.npy
./keypoints/07070.npy
./keypoints/07099.npy
./keypoints/07074.npy
(50, 1662)
./keypoints/69302.npy
./keypoints/65539.npy
(50, 1662)
./keypoints/17710.npy
./keypoints/17733.npy
./keypoints/65540.npy
(50, 1662)
./keypoints/17734.npy
./keypoints/17711.npy
./keypoints/17712.npy
(50, 1662)
./keypoints/17713.npy
./keypoints/17709.npy
./keypoints/17720.npy
(50, 1662)
./keypoints/17721.npy
(50, 1662)
./keypoints/17722.npy
(50, 1662)
./keypoints/17723.npy
./keypoints/17724.npy
(50, 1662)
./keypoints/12328.npy
./keypoints/12312.npy
./keypoints/12311.npy
./keypoints/12338.npy
./keypoints/12313.npy
./keypoints/12314.npy
(50, 1662)
./keypoints/12315.npy
./keypoints/12316.npy
(50, 1662)
./keypoints/12317.npy
./keypoints/12318.npy
(50, 1662)
./keypoints/12319.npy
(50, 1662)
./keypoints/12320.npy
./keypoints/12326.npy
./keypoints/12327.npy
(50, 1662)
./keypoints/05728.npy
(50, 1662)
./keypoints/05749.npy
./keypoints/057

In [32]:
X = np.array(data_sequence)

label_encoder = LabelEncoder()
int_labels = label_encoder.fit_transform(np.array(label_sequence))

y = to_categorical(int_labels)

label_sequence

['book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'book',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'drink',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'computer',
 'before',
 'before',
 'before',
 'before',
 'before',
 'before',
 'before',
 'before',
 'before',
 'before',
 'before',


In [33]:
int_labels

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 6, 6, 6, 6, 6, 6, 6, 6, 6,
       6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6,
       6, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5,
       5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 7,
       7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 8, 8, 8, 8, 8, 8, 8, 8,
       8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8,
       8, 8, 8, 8, 8, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2])

In [18]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.05)

X_train.shape, X_test.shape, y_train.shape, y_test.shape

((209, 50, 1662), (11, 50, 1662), (209, 9), (11, 9))

## Build LSTM Model

In [38]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.callbacks import TensorBoard
from tensorflow.keras.metrics import CategoricalAccuracy

In [39]:
log_dir = os.path.join('Logs')
output_shape = X_test.shape[0]
output_shape

11

In [40]:
frames = 50
output_shape = y_test.shape[1]

model = Sequential()

model.add(LSTM(64, return_sequences=True, activation='relu', input_shape=(frames, 1662)))
model.add(LSTM(128, return_sequences=True, activation='relu'))
model.add(LSTM(64, return_sequences=False, activation='relu'))
model.add(Dense(64, activation='relu'))
model.add(Dense(32, activation='relu'))
model.add(Dense(output_shape, activation='softmax'))

In [42]:
model.compile(
    optimizer="Adam",
    loss='categorical_crossentropy',
    metrics=[CategoricalAccuracy()]
)

In [43]:
lr = 0.01
batch_size = 64
epochs = 200
callbacks = TensorBoard(log_dir=log_dir)

history = model.fit(
    x=X_train,
    y=y_train,
    batch_size=batch_size,
    epochs=epochs,
    verbose="auto",
    callbacks=callbacks
)

Epoch 1/200
4/4 [==============================] - 2s 50ms/step - loss: 8.7077 - categorical_accuracy: 0.1244
Epoch 2/200
4/4 [==============================] - 0s 61ms/step - loss: 51.9655 - categorical_accuracy: 0.0909
Epoch 3/200
4/4 [==============================] - 0s 59ms/step - loss: 37.1330 - categorical_accuracy: 0.1531
Epoch 4/200
4/4 [==============================] - 0s 61ms/step - loss: 46.4074 - categorical_accuracy: 0.1627
Epoch 5/200
4/4 [==============================] - 0s 62ms/step - loss: 783.6586 - categorical_accuracy: 0.1435
Epoch 6/200
4/4 [==============================] - 0s 61ms/step - loss: 14796.8311 - categorical_accuracy: 0.1100
Epoch 7/200
4/4 [==============================] - 0s 64ms/step - loss: 14341.8809 - categorical_accuracy: 0.1148
Epoch 8/200
4/4 [==============================] - 0s 60ms/step - loss: 5785.1387 - categorical_accuracy: 0.1100
Epoch 9/200
4/4 [==============================] - 0s 59ms/step - loss: 3822.0344 - categorical_accuracy

In [36]:
history.history

{'loss': [1.9255317449569702,
  1.9308967590332031,
  1.927256464958191,
  1.9266058206558228,
  1.9299888610839844,
  1.922329068183899,
  1.915406346321106,
  1.9246934652328491,
  1.9265985488891602,
  1.918972373008728,
  1.916015625,
  1.9182542562484741,
  1.9162838459014893,
  1.9174927473068237,
  1.9165657758712769,
  1.9227484464645386,
  1.9120874404907227,
  1.917276382446289,
  1.9193278551101685,
  1.9139457941055298,
  1.9090242385864258,
  1.911529541015625,
  1.911655068397522,
  1.910279393196106,
  1.9155553579330444,
  1.9131572246551514,
  1.910158634185791,
  1.9190869331359863,
  1.9091497659683228,
  1.9091945886611938,
  1.9065428972244263,
  1.918493628501892,
  1.9042448997497559,
  1.910301923751831,
  1.9130171537399292,
  1.9011598825454712,
  1.9005088806152344,
  1.9011471271514893,
  1.9032363891601562,
  1.8997697830200195,
  1.8987680673599243,
  1.899444580078125,
  1.9015036821365356,
  1.8989524841308594,
  1.9041976928710938,
  1.898819923400879,


In [27]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm (LSTM)                 (None, 50, 64)            442112    
                                                                 
 lstm_1 (LSTM)               (None, 50, 128)           98816     
                                                                 
 lstm_2 (LSTM)               (None, 64)                49408     
                                                                 
 dense (Dense)               (None, 64)                4160      
                                                                 
 dense_1 (Dense)             (None, 32)                2080      
                                                                 
 dense_2 (Dense)             (None, 9)                 297       
                                                                 
Total params: 596873 (2.28 MB)
Trainable params: 596873 

In [30]:
res = model.predict(X_test)

1/1 [==============================] - 0s 19ms/step


(11, 9)

In [45]:
print("Evaluate on test data")
results = model.evaluate(X_test, y_test, batch_size=128)
print("test loss, test acc:", results)

Evaluate on test data
1/1 [==============================] - 0s 208ms/step - loss: 18.4216 - categorical_accuracy: 0.0909
test loss, test acc: [18.421588897705078, 0.09090909361839294]
